In [273]:
import numpy as np
import h5py

with h5py.File("../data/results/hv_lightmap.h5", "r") as f:
    positions = np.array(list(zip(f["posX"], f["posY"], f["posZ"])))
    pte = np.array([f[f"ch{i:02d}_pte"] for i in range(2)]).T

In [295]:
# 1. find pitch per coordinate, i.e. smallest non-zero difference
# between any two positions
diffs = positions - positions[0]
pitch = []
for i in range(3):
    col = np.abs(diffs[:, i])
    pitch.append(np.min(np.abs(col[col != 0])))
pitch = np.array(pitch)
print(pitch)

# 2. generate bbox bounds
bbox_min = []
bbox_max = []
for i in range(3):
    bbox_min.append(np.min(positions[:, i]) - pitch[i] / 2)
    bbox_max.append(np.max(positions[:, i]) + pitch[i] / 2)
bounds = np.array([bbox_min, bbox_max])
print(bounds)

# 3. Create lightmap grid
x = np.arange(bounds[0, 0] + pitch[0] / 2, bounds[1, 0], pitch[0])
y = np.arange(bounds[0, 1] + pitch[1] / 2, bounds[1, 1], pitch[1])
z = np.arange(bounds[0, 2] + pitch[2] / 2, bounds[1, 2], pitch[2])

# this is how photon library is created:
# - always attempt to increment x
# - if x is at the end, increment y and reset x
# - if y is at the end, increment z and reset y and x
# - if z is at the end, you're done
X, Y, Z = np.meshgrid(x, y, z, indexing="ij")
all_pos = np.column_stack((X.ravel(), Y.ravel(), Z.ravel()))
voxel_shape = (len(x), len(y), len(z))
sorted_indices = np.lexsort((all_pos[:, 0], all_pos[:, 1], all_pos[:, 2]))
all_pos = all_pos[sorted_indices]
# 4. Fill lightmap grid with values, setting zero for missing values
full_values = np.full(shape=(all_pos.shape[0], pte.shape[1]), fill_value=0, dtype=float)
starting_point = bbox_min + pitch / 2

indices = np.round((positions - starting_point) / pitch).astype(int)
linear_indices = np.ravel_multi_index(indices.T, voxel_shape)
full_values[linear_indices] = pte
full_values = full_values[sorted_indices]

import trimesh

pc = trimesh.PointCloud(all_pos)
pc.colors = trimesh.visual.interpolate(
    np.log10(full_values[:, 0] + 1e-8), color_map="viridis"
)

# # 5. Create PhotonLib object
from photonlib import PhotonLib, VoxelMeta

meta = VoxelMeta(shape=(len(x), len(y), len(z)), ranges=bounds.T)
p = meta.voxel_to_coord(range(full_values.shape[0]))
# PhotonLib.save("../data/results/hv_lightmap.plib", full_values, meta)

[5. 5. 5.]
[[127.5 232.5 277.5]
 [327.5 432.5 392.5]]


In [296]:
trimesh.Scene([pc]).show()

In [263]:
p = plib.meta.voxel_to_coord(range(full_values.shape[0]))

pc = trimesh.PointCloud(p)
pc.colors = trimesh.visual.interpolate(np.log10(plib.vis[:, 0] + 1e-8), color_map="viridis")
trimesh.Scene([pc]).show()

In [249]:
full_values.shape

(36800, 2)

In [247]:
# plot with trimesh to see how we did
import trimesh

# nan_pos = all_pos[np.isnan(full_values)]
# other = all_pos[~np.isnan(full_values)]
# other_pte = full_values[~np.isnan(full_values)]

# # nanpc = trimesh.PointCloud(nan_pos)
# # nanpc.colors = [255, 0, 0, 255]

otherpc = trimesh.PointCloud(all_positions)
otherpc.colors = [0,0,0,1]
# set color to viridis using pte
otherpc.colors = trimesh.visual.color.interpolate(
    np.log10(full_values[:,0] + 1e-8), "viridis"
)

scene = trimesh.Scene([otherpc])
scene.show()

In [248]:
plib = PhotonLib.load("../data/results/hv_lightmap.plib")
vis = plib.vis
positions = plib.meta.voxel_to_coord(range(vis.shape[0]))

import trimesh

pc = trimesh.PointCloud(positions)
pc.colors = trimesh.visual.color.interpolate(np.log10(vis[:, 0] + 1e-8), "viridis")
trimesh.Scene([pc]).show()

[PhotonLib] loading ../data/results/hv_lightmap.plib
[PhotonLib] file loaded
